In [16]:
import pandas as pd
import re
import html
import requests
from bs4 import BeautifulSoup, Tag


In [44]:
data = pd.read_csv("alabama.csv")
data.head()
statesname = ['Alabama', 'Alaska', 'Arizona', 'Arkansas', 'California', 'Colorado', 'Connecticut', 'Delaware', 'District of Columbia', 'Florida', 'Georgia', 'Hawaii', 'Idaho', 'Illinois', 'Indiana', 'Iowa', 'Kansas', 'Kentucky', 'Louisiana', 'Maine', 'Montana', 'Nebraska', 'Nevada', 'New Hampshire', 'New Jersey', 'New Mexico', 'New York', 'North Carolina', 'North Dakota', 'Ohio', 'Oklahoma', 'Oregon', 'Maryland', 'Massachusetts', 'Michigan', 'Minnesota', 'Mississippi', 'Missouri', 'Pennsylvania', 'Rhode Island', 'South Carolina', 'South Dakota', 'Tennessee', 'Texas', 'Utah', 'Vermont', 'Virginia', 'Washington', 'West Virginia', 'Wisconsin', 'Wyoming']
myurl = data["SEC LINK"].tolist()

In [26]:
def text_between1(substring_start, substring_end, text):
    substring_start = substring_start.lower()
    substring_end = substring_end.lower()
    start_index = text.find(substring_start)
    end_index = text.find(substring_end)
#    if start_index == -1 or end_index == -1:
#        raise StringBetweenException(
#            "Substring not found: {}".format(substring_start))
    start_index += len(substring_start)
    return text[start_index:end_index]

In [27]:
def findtext(string,substring):
    i=string.lower().find(substring)
    e=string.lower().find(substring,i+1)
    return (max(i,e))

In [28]:
def text_between(substring_start, substring_end, text):
    substring_start = substring_start.lower()
    substring_end = substring_end.lower()
    start_index = findtext(text,substring_start)
    end_index = findtext(text,substring_end)
#    if start_index == -1 or end_index == -1:
#        raise StringBetweenException(
#            "Substring not found: {}".format(substring_start))
#    start_index += len(substring_start)
    return text[start_index:end_index]

In [29]:
def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', raw_html)
    cleantext=cleantext.replace('&nbsp;',' ')
    cleantext=cleantext.replace('\xa0',' ')
    cleantext=cleantext.replace('\n',' ')
        
    return cleantext

In [30]:
def subplace(text):
    if (text).count('Item 1.')>1:
        text.replace('Item 1.', 'XXX', 1)
    if (text).count('Item 2.')>1:
        text.replace('Item 2.', 'XXX', 1)
    if (text).count('Item 3.')>1:
        text.replace('Item 3.', 'XXX', 1)
    if (text).count('Item 6.')>1:
        text.replace('Item 6.', 'XXX', 1)
    if (text).count('Item 7.')>1:
        text.replace('Item 7.', 'XXX', 1)
    if (text).count('Item 8.')>1:
        text.replace('Item 8.', 'XXX', 1)
    return (text)

In [45]:
finaldf=pd.DataFrame()
my_dict={}
filecount=0

In [49]:
myurl_length = len(myurl)
for i in range(myurl_length):
    print(myurl[i])
    f = requests.get(myurl[i])
    data1 = f.text
    soup = BeautifulSoup(data1,"lxml")
    #for tag in soup.find_all('A'):
        #data1=re.sub("<[A][^>]*>(.+?)</[A]>", '', data1)
        #tag.decompose()
    #data1= data1.replace("\\<A(.*)A>", "");
    #data1=soup.get_text()
    data1=cleanhtml(data1)
        
    try:
        item1= subplace((text_between("ITEM 1","ITEM 2", data1)))
    except:
        pass
    try:
        item2= subplace((text_between("ITEM 2","ITEM 3", data1)))
    except:
        pass
    #item1= text_beteen("ITEM 1","ITEM 2", data)
    try:
        item6 = subplace(text_between("ITEM 6","ITEM 7", data1))
    except :
        pass
    try:
        item7 = subplace(text_between("ITEM 7","ITEM 8", data1))
    except :
        pass
    try:
        from_date = subplace(text_between("FILED AS OF DATE:","FILER:", data1))
    except :
        pass
    try:
        company_name = ' '.join((text_between("COMPANY CONFORMED NAME:","CENTRAL INDEX KEY:", data1)).split())
    except :
        pass
    try:
        cik = ' '.join((text_between("CENTRAL INDEX KEY:","STANDARD INDUSTRIAL CLASSIFICATION:", data1)).split())
    except :
        pass
    try:
        incorporation = ' '.join((text_between("STATE OF INCORPORATION:","FISCAL YEAR END:", data1)).split())
    except :
        pass
    try:
        staten = ' '.join((text_between("STATE:","ZIP:", data1)).split())
    except :
        pass
    try:
        addzip = ' '.join((text_between("STATE","BUSINESS PHONE:", data1)).split())
    except :
        pass
    finalstr=item1+item2+item6+item7
    #    companyname=companyname.strip()
    #    complist.append(companyname)
    #    item1list=item1.split()
    filtered_words = ' '.join([word for word in finalstr.split()])
    #[word for word in item1list if word not in stopwords.words('english')]

    for i in statesname:
        my_count = finalstr.count(i)
        my_dict['Company']=company_name[24:]
        my_dict['cik']=cik[19:29] 
        my_dict['incorporation']=incorporation[24:27]
        my_dict['staten']=staten[7:10]
        my_dict['addzip'] = addzip[15:]
        my_dict['from_date']=from_date[19:27]
        my_dict[i]=my_count
        #print (my_dict)
        mydf=pd.DataFrame(my_dict, index=['i',])

    #    finaldf1.append(finaldf, ignore_index=True)
    #    finaldf1.to_csv('C:\\Users\\jeet\\Desktop\\SEC\\final_file.csv', sep=',', encoding='utf-8',)

        #print(mydf)
        
    finaldf= finaldf.append(mydf, ignore_index=True)
    finaldf.to_csv('file12.csv', sep=',', encoding='utf-8',)
    print(filecount)
    filecount+=1

http://www.sec.gov/Archives/edgar/data/1109537/000104746905006453/0001047469-05-006453.txt
133
http://www.sec.gov/Archives/edgar/data/1109537/000110465906018622/0001104659-06-018622.txt
134
http://www.sec.gov/Archives/edgar/data/1307969/000168316817000653/0001683168-17-000653.txt
135
http://www.sec.gov/Archives/edgar/data/1050122/000092735699000620/0000927356-99-000620.txt
136
http://www.sec.gov/Archives/edgar/data/1050122/000092735600000660/0000927356-00-000660.txt
137
http://www.sec.gov/Archives/edgar/data/1050122/000092735601000365/0000927356-01-000365.txt
138
http://www.sec.gov/Archives/edgar/data/1050122/000091205702012585/0000912057-02-012585.txt
139
http://www.sec.gov/Archives/edgar/data/1050122/000110465903005254/0001104659-03-005254.txt
140
http://www.sec.gov/Archives/edgar/data/1050122/000110465904007882/0001104659-04-007882.txt
141
http://www.sec.gov/Archives/edgar/data/1050122/000104746905006925/0001047469-05-006925.txt
142
http://www.sec.gov/Archives/edgar/data/1050122/000

KeyboardInterrupt: 

In [22]:
subplace((data1))

'0001193125-14-383437.txt : 20141027 0001193125-14-383437.hdr.sgml : 20141027 20141027171155 ACCESSION NUMBER:\t\t0001193125-14-383437 CONFORMED SUBMISSION TYPE:\t10-K PUBLIC DOCUMENT COUNT:\t\t18 CONFORMED PERIOD OF REPORT:\t20140927 FILED AS OF DATE:\t\t20141027 DATE AS OF CHANGE:\t\t20141027  FILER:  \tCOMPANY DATA:\t \t\tCOMPANY CONFORMED NAME:\t\t\tAPPLE INC \t\tCENTRAL INDEX KEY:\t\t\t0000320193 \t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tELECTRONIC COMPUTERS [3571] \t\tIRS NUMBER:\t\t\t\t942404110 \t\tSTATE OF INCORPORATION:\t\t\tCA \t\tFISCAL YEAR END:\t\t\t0927  \tFILING VALUES: \t\tFORM TYPE:\t\t10-K \t\tSEC ACT:\t\t1934 Act \t\tSEC FILE NUMBER:\t000-10030 \t\tFILM NUMBER:\t\t141175110  \tBUSINESS ADDRESS:\t \t\tSTREET 1:\t\tONE INFINITE LOOP \t\tCITY:\t\t\tCUPERTINO \t\tSTATE:\t\t\tCA \t\tZIP:\t\t\t95014 \t\tBUSINESS PHONE:\t\t(408) 996-1010  \tMAIL ADDRESS:\t \t\tSTREET 1:\t\tONE INFINITE LOOP \t\tCITY:\t\t\tCUPERTINO \t\tSTATE:\t\t\tCA \t\tZIP:\t\t\t95014  \tFORMER COMPANY:\t

In [55]:
item1

''